In [11]:
import pandas as pd
import numpy as np

# Load the data
url= "https://raw.githubusercontent.com/stawiskm/pythoncourse/student/Assignments/Data/fictitious_hospital_data.csv"
data = pd.read_csv(url)

# 1. Data Cleaning
# -----------------

# Check for missing values
missing_values = data.isnull().sum()
print("Missing values in each column:")
print(missing_values)

# Drop rows with missing values (if any)
data_cleaned = data.dropna()

# Check for duplicate rows
duplicate_rows = data_cleaned.duplicated().sum()
# print(f"Number of duplicate rows: {duplicate_rows}")

# Drop duplicate rows (if any)
data_cleaned = data_cleaned.drop_duplicates()

# Standardize categorical data (convert to lower case or consistent format)
data_cleaned['Gender'] = data_cleaned['Gender'].str.lower()
data_cleaned['Primary_Diagnosis'] = data_cleaned['Primary_Diagnosis'].str.lower()
data_cleaned['Discharge_Destination'] = data_cleaned['Discharge_Destination'].str.lower()

# 2. Feature Engineering
# ----------------------

# Create a new feature: Length of Stay Category
bins = [0, 3, 7, 14, np.inf]
labels = ['Short', 'Medium', 'Long', 'Very Long']
data_cleaned['Length_of_Stay_Category'] = pd.cut(data_cleaned['Length_of_Stay'], bins=bins, labels=labels)

# Create a new feature: Age Group
age_bins = [0, 30, 50, 70, np.inf]
age_labels = ['Young', 'Middle-aged', 'Senior', 'Elderly']
data_cleaned['Age_Group'] = pd.cut(data_cleaned['Age'], bins=age_bins, labels=age_labels)

# Create a new feature: Comorbidity Burden
data_cleaned['Comorbidity_Burden'] = pd.cut(data_cleaned['Num_Comorbidities'], bins=[-1, 0, 2, 4, np.inf], labels=['None', 'Low', 'Medium', 'High'])

# 3. Data Analysis
# ----------------

# Analyzing Readmission Rates by Various Factors

# Readmission rate by Gender
readmission_by_gender = data_cleaned.groupby('Gender')['Readmitted_Within_30_Days'].mean()
print("Readmission rate by Gender:")
print(readmission_by_gender)

# Readmission rate by Primary Diagnosis
readmission_by_diagnosis = data_cleaned.groupby('Primary_Diagnosis')['Readmitted_Within_30_Days'].mean()
print("\nReadmission rate by Primary Diagnosis:")
print(readmission_by_diagnosis)

# Readmission rate by Length of Stay Category
readmission_by_los = data_cleaned.groupby('Length_of_Stay_Category')['Readmitted_Within_30_Days'].mean()
print("\nReadmission rate by Length of Stay Category:")
print(readmission_by_los)

# Readmission rate by Age Group
readmission_by_age_group = data_cleaned.groupby('Age_Group')['Readmitted_Within_30_Days'].mean()
print("\nReadmission rate by Age Group:")
print(readmission_by_age_group)

# Readmission rate by Discharge Destination
readmission_by_discharge = data_cleaned.groupby('Discharge_Destination')['Readmitted_Within_30_Days'].mean()
print("\nReadmission rate by Discharge Destination:")
print(readmission_by_discharge)

# Readmission rate by Comorbidity Burden
readmission_by_comorbidity = data_cleaned.groupby('Comorbidity_Burden')['Readmitted_Within_30_Days'].mean()
print("\nReadmission rate by Comorbidity Burden:")
print(readmission_by_comorbidity)

# Summary Statistics for Data
summary_stats = data_cleaned.describe()
print("\nSummary statistics of cleaned data:")
print(summary_stats)

# Count of patients in each group (e.g., Age Group, Length of Stay Category)
age_group_counts = data_cleaned['Age_Group'].value_counts()
length_of_stay_counts = data_cleaned['Length_of_Stay_Category'].value_counts()

print("\nCount of patients by Age Group:")
print(age_group_counts)

print("\nCount of patients by Length of Stay Category:")
print(length_of_stay_counts)

# Correlation Matrix
# Convert categorical features to numerical using one-hot encoding
data_cleaned = pd.get_dummies(data_cleaned)
# Correlation matrix for numerical features
correlation_matrix = data_cleaned.corr()
print("\nCorrelation matrix: of values abs(corr) > 0.8")
# format the output only show the values that are greater than 0.8 in absolute value
# Output: feature 1 vs feature 2 : correlation value and only show the values that are greater than 0.8 in absolute value
print(correlation_matrix[(correlation_matrix.abs() > 0.8) & (correlation_matrix < 1)].stack().dropna())


Missing values in each column:
Patient_ID                   0
Age                          0
Gender                       0
Primary_Diagnosis            0
Num_Comorbidities            0
Length_of_Stay               0
Discharge_Destination        0
Follow_Up_Appointment        0
Readmitted_Within_30_Days    0
dtype: int64
Readmission rate by Gender:
Gender
female    0.136364
male      0.160714
Name: Readmitted_Within_30_Days, dtype: float64

Readmission rate by Primary Diagnosis:
Primary_Diagnosis
copd              0.153846
diabetes          0.192308
heart failure     0.200000
kidney disease    0.058824
pneumonia         0.125000
Name: Readmitted_Within_30_Days, dtype: float64

Readmission rate by Length of Stay Category:
Length_of_Stay_Category
Short        0.6
Medium       0.0
Long         0.0
Very Long    0.0
Name: Readmitted_Within_30_Days, dtype: float64

Readmission rate by Age Group:
Age_Group
Young          0.190476
Middle-aged    0.260870
Senior         0.103448
Elderly        

In [17]:
import pandas as pd
# Url
url1 = "https://raw.githubusercontent.com/stawiskm/pythoncourse/student/Assignments/Data/fictitious_patients.csv"
url2 = "https://raw.githubusercontent.com/stawiskm/pythoncourse/student/Assignments/Data/fictitious_visits.csv"
# Load the datasets
patients_df = pd.read_csv(url1)
visits_df = pd.read_csv(url2)

# 1. Data Merging: Combine patients and visits data into a single DataFrame
# Assume there's a common column 'Patient_ID' in both datasets
merged_df = pd.merge(visits_df, patients_df, on='Patient_ID', how='inner')

# 2. Adherence Calculation: Calculate medication adherence rates
# Adherence Rate = (Reported Doses Taken / Prescribed Doses) * 100
merged_df['Adherence_Rate'] = (merged_df['Reported_Doses_Taken'] / merged_df['Prescribed_Doses']) * 100

# 3. Risk Stratification: Classify patients into risk categories based on adherence rate
def classify_adherence(rate):
    if rate >= 80:
        return 'High'
    elif 50 <= rate < 80:
        return 'Medium'
    else:
        return 'Low'

merged_df['Adherence_Level'] = merged_df['Adherence_Rate'].apply(classify_adherence)

# Analyze characteristics of each group
# Grouping by Adherence Level and aggregating other characteristics
grouped_df = merged_df.groupby('Adherence_Level').agg({
    'Age': 'mean',
    'Num_Medications': 'mean',
    'Condition': pd.Series.mode,
    'Patient_ID': 'nunique'  # Count of unique patients in each adherence group
}).reset_index()

# Output the results
print(grouped_df)

# Example: Flag patients with low adherence for additional support
low_adherence_patients = merged_df[merged_df['Adherence_Level'] == 'Low']
print("Patients at high risk of non-adherence:")
print(low_adherence_patients[['Patient_ID', 'Age']].drop_duplicates())


  Adherence_Level        Age  Num_Medications                Condition  \
0            High  52.164444         4.333333             Hypertension   
1             Low  75.969697        10.166667             Hypertension   
2          Medium  72.222222        10.000000  Hypertension & Diabetes   

   Patient_ID  
0          70  
1          24  
2           8  
Patients at high risk of non-adherence:
     Patient_ID  Age
1             2   84
5            13   85
26           73   68
28           17   67
115          11   75
125          37   76
128           5   72
131          83   72
140          89   80
162          97   73
171          23   70
179          53   73
185          67   72
188           7   71
191          29   76
230          31   81
232          47   71
254          43   83
273          41   67
287          59   76
289          71   86
294          61   79
298          19   85
299           3   79
